In [1]:
import h5py, numpy
from pycbc.conversions import mchirp_from_mass1_mass2

f = h5py.File('../combined.hdf', 'r')
m1b = f['mass1'][:]
m2b = f['mass2'][:]
mcb = mchirp_from_mass1_mass2(m1b, m2b)
print len(m1b)

4030479


In [2]:
import os
os.environ['HMR_FILE'] = '../s.hdf'
from pycbc.waveform import get_td_waveform, get_fd_waveform
import pycbc.psd
from pycbc.filter import match

bf = 128
sr = 4096
tlen = bf * sr
flen = int(tlen / 2 + 1)
fl = 20
df = 1.0 / bf
dt = 1.0 / sr

p = pycbc.psd.from_txt('../H1L1-AVERAGE_PSD-1163174417-604800.txt', flen, df, fl)

### EOB mathes HMR model ###

In [3]:
m1 = 21
m2 = 0.1
hp, hc = get_td_waveform(approximant="EOBNRv2", mass1=m1, mass2=m2, f_lower=fl,
                         delta_t=dt, coa_phase=0.3)

if len(hp) > tlen:
    hp = hp[len(hp)-tlen:]
hp.resize(tlen)

if len(hc) > tlen:
    hc = hc[len(hc)-tlen:]
hc.resize(tlen) 

hp2, hc2 = get_fd_waveform(approximant="HMR", mass1=m1, mass2=m2, f_lower=fl, delta_f=df)
hp2.resize(flen)
import pylab

hp2 = hp2.to_timeseries()

pylab.plot(hp.sample_times, hp)
pylab.plot(hp2.sample_times, hp2)
match(hp, hp2, psd=p, low_frequency_cutoff=20)

(0.9901870809698488, 204)

### Bank is reasonably self-consistent ###

In [4]:
from pycbc.conversions import tau0_from_mass1_mass2

m1 = 20
m2 = .012

tau0 = tau0_from_mass1_mass2(m1, m2, 15.0)
tau0b = tau0_from_mass1_mass2(m1b, m2b, 15.0)

k = abs(tau0 - tau0b) < 1.0
m1t = m1b[k]
m2t = m2b[k]
print len(m1t)


#hp, hc = get_td_waveform(approximant="EOBNRv2", mass1=m1, mass2=m2, f_lower=fl,
#                         delta_t=dt, coa_phase=0.3)

#if len(hp) > tlen:
#    hp = hp[len(hp)-tlen2:]
#hp.resize(tlen)

#if len(hc) > tlen:
#    hc = hc[len(hc)-tlen2:]
#hc.resize(tlen)    
hp, hc = get_fd_waveform(approximant="HMR", mass1=m1, mass2=m2, delta_f=df, f_lower=fl, duration=30.0)
hp.resize(flen)

ff = 0
for m1g, m2g in zip(m1t, m2t):
    hp2, hc2 = get_fd_waveform(approximant="HMR", mass1=m1g, mass2=m2g, f_lower=fl, delta_f=df, duration=30.0)
    hp2.resize(flen)

    m = match(hp, hp2, psd=p**0.5, low_frequency_cutoff=25)[0]
    if m > ff:
        ff = m
        print ff, m1g, m2g
    if ff > 0.97:
        break

684
0.08255756533995576 0.010500862528156466 24.435731201494217
0.446711279681257 0.011960072405172769 20.104449891420213
0.5188049320733286 0.011972698451323012 20.071213945176893
0.8501227180221123 0.011995199352720002 20.015618293538672


In [5]:
m1 = 20
m2 = .011

from pycbc.conversions import tau0_from_mass1_mass2
tau0 = tau0_from_mass1_mass2(m1, m2, 15.0)
tau0b = tau0_from_mass1_mass2(m1b, m2b, 15.0)

print tau0, tau0b

k = abs(tau0 - tau0b) < 1.0
m1t = m1b[k]
m2t = m2b[k]
print len(m1t)


5834.5144175 [  22.57665414   22.96901105   22.5275006  ... 6307.96435121 6307.96616623
 6306.65526576]
253


### Higher modes ####

In [6]:
for m1 in [20.0, 50.0, 100.0]:
    for m2 in [1, .1, .05, .01]:
        inc = [0, 1.0, 1.4, 1.7]
        for i in inc:
            hp, hc = get_td_waveform(approximant="EOBNRv2HM", mass1=m1, mass2=m2, f_lower=fl, delta_t=dt, inclination=i, coa_phase=0.3)

            print len(hp)
            if len(hp) > tlen:
                hp = hp[len(hp)-tlen:]
            hp.resize(tlen)

            if len(hc) > tlen:
                hc = hc[len(hc)-tlen:]
            hc.resize(tlen)    

            hp2, hc2 = get_fd_waveform(approximant="HMR", mass1=m1, mass2=m2, f_lower=fl, delta_f=df)
            fmin = hp2.sample_frequencies[hp2.abs_arg_max()]
            
            fcut = int(fmin) + 5
            print "FLOW", fmin, fcut
            
            hp2.resize(flen)

            o1 = match(hp, hp2, psd=p, low_frequency_cutoff=fcut)[0]
            o2 = match(hc, hp2, psd=p, low_frequency_cutoff=fcut)[0]
            o3 = match(hp, hc, psd=p, low_frequency_cutoff=fcut)[0]

            print m1, m2, i, o1, o2, o3

119744
FLOW 20.4375 25
20.0 1 0 0.9991122917661194 0.9991324282362697 0.9999166890989953
119744
FLOW 20.4375 25
20.0 1 1.0 0.9340382608218135 0.9359615203487378 0.9994996392171887
119744
FLOW 20.4375 25
20.0 1 1.4 0.9080373801212465 0.9126884300242499 0.9982966747515735
119744
FLOW 20.4375 25
20.0 1 1.7 0.9067710248865075 0.9116046131346238 0.9981977501870551
1174277
FLOW 29.4765625 34
20.0 0.1 0 0.9987556640029341 0.998773022368359 0.9999876522518931
1174277
FLOW 29.4765625 34
20.0 0.1 1.0 0.9225480386048182 0.9237008266616376 0.9997349907014267
1174277
FLOW 29.4765625 34
20.0 0.1 1.4 0.8935738238396997 0.8963952529049806 0.9990175757188763
1174277
FLOW 29.4765625 34
20.0 0.1 1.7 0.8921906995490146 0.8951275776894501 0.9989588215059407
2345890
FLOW 37.484375 42
20.0 0.05 0 0.9899859747491441 0.9899856021006652 0.9999919744335682
2345890
FLOW 37.484375 42
20.0 0.05 1.0 0.8883187400793041 0.9012106235536826 0.9965686658565688
2345890
FLOW 37.484375 42
20.0 0.05 1.4 0.8364520129605985 0.